# CSE 251C Project Experiments

## Initial Setup

In [11]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [22]:
import torch
from torch import nn, optim
from torchvision.datasets import MNIST, CIFAR10
from torchvision import transforms
from torch.utils.data import DataLoader, Dataset
from tqdm import tqdm_notebook
from pathlib import Path
import json

# for each different seed value, completely different experiments will run
SEED = 123
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda')

## Model Definitions

In [23]:
class MLP(nn.Module):
    def __init__(self, in_size, out_size, width, depth):
        super().__init__()
        self.width = width
        self.depth = depth
        
        layers = [
            nn.Flatten(),
            nn.Linear(in_size, width), 
            nn.ReLU(),
        ]

        for i in range(depth):
            layers.append(nn.Linear(width, width))
            layers.append(nn.ReLU())
        
        layers.append(nn.Linear(width, out_size))

        self.model = nn.Sequential(*layers)

    def forward(self, x):
        return self.model(x)

    def __repr__(self):
        # function that gives you a representation you can save the model with
        return f'MLPw{self.width}d{self.depth}'

## Dataset and Loader Definitions

In [24]:
def get_io_params_for_dataset(dataset_name):
    if dataset_name == 'mnist':
        in_size = 28 * 28
        out_size = 10
    elif dataset_name == 'cifar10':
        in_size = 32 * 32 * 3
        out_size = 10
    else:
        raise ValueError(f'Dataset "{dataset_name}" unknown.')

    return in_size, out_size

In [25]:
def get_dataset_class_and_normalization(dataset_name):
    if dataset_name == 'mnist':
        dataset_class = MNIST
        normalization = [(0.1307,), (0.3081,)]
    elif dataset_name == 'cifar10':
        dataset_class = CIFAR10
        normalization = [(0.4914, 0.4822, 0.4465), (0.247, 0.243, 0.261)]
    else:
        raise ValueError(f'Dataset "{dataset_name}" unknown.')

    return dataset_class, normalization

In [26]:
def get_data(dataset_name):
    dataset_class, normalization = get_dataset_class_and_normalization(dataset_name)

    train_set = dataset_class(
        dataset_name,
        train=True, 
        download=True,
        transform=transforms.Compose([
            transforms.ToTensor(),
            transforms.Normalize(*normalization),                                                                   
        ]),
    )

    test_set = dataset_class(
        dataset_name,
        train=False, 
        download=True,
        transform=transforms.Compose([
            transforms.ToTensor(),
            transforms.Normalize(*normalization),                                                                   
        ]),
    )

    train_set.targets = torch.LongTensor(train_set.targets)

    # unmodified train/test set
    return train_set, test_set

In [27]:
class Noisy(Dataset):
    def __init__(self, *args, dataset_name='', percent_corruption=0, corruption_order=None, corrupted_labels=None, **kwargs):
        super().__init__(*args, **kwargs)

        dataset_class, normalization = get_dataset_class_and_normalization(dataset_name)

        self.noisy_dataset = dataset_class(
            dataset_name,
            train=True, 
            download=True,
            transform=transforms.Compose([
                transforms.ToTensor(),
                transforms.Normalize(*normalization),                                                                   
            ]),
        )

        self.noisy_dataset.targets = torch.LongTensor(self.noisy_dataset.targets)
        sample_size = self.noisy_dataset.targets.size(0)
        corrupted_sample_count = int(percent_corruption * sample_size / 100)
        # corrupt indices in a random, but predictable order
        corrupted_sample_indices = corruption_order[:corrupted_sample_count]

        # unmodified =        original index       [ 0,  1,  2, ...]
        # modified   = (-1) * original index - 1   [-1, -2, -3, ...]
        self.target_indexes = torch.arange(sample_size)
        self.target_indexes[corrupted_sample_indices] = (-1) * self.target_indexes[corrupted_sample_indices] - 1

        # modify labels
        self.noisy_dataset.targets[corrupted_sample_indices] = corrupted_labels[corrupted_sample_indices]

        # for convenience
        self.data = self.noisy_dataset.data
        self.targets = self.noisy_dataset.targets

    def __len__(self):
        return len(self.noisy_dataset)

    def __getitem__(self, idx):
        features, label = self.noisy_dataset[idx]  # should handle its own transform
        target_index = self.target_indexes[idx]

        return features, target_index, label

## Train and Test Functions

In [28]:
def get_indexes_where(condition_tensor):
    index_tensor = condition_tensor.nonzero()
    return index_tensor if index_tensor.nelement() == 0 else index_tensor[:, 0]

def safe_argmax(logits):
    return logits if logits.nelement() == 0 else logits.argmax(dim=-1)

def train_once(network, optimizer, criterion, train_loader):
    # actual training
    network.train()
    epoch_loss = 0

    for batch_idx, (data, _, target) in enumerate(tqdm_notebook(train_loader, desc='Train', leave=False)):
        optimizer.zero_grad()

        data = data.to(device)
        target = target.to(device)
        
        output = network(data)

        loss = criterion(output, target)
        loss.backward()
        optimizer.step()

        epoch_loss += loss.item() * data.size(0)

    return epoch_loss / len(train_loader.sampler)

def get_incorrect_once(network, optimizer, nograd_train_loader):
    # incorrect predictions check
    network.eval()
    regular_incorrect_indexes_dict = {}
    corrupt_incorrect_indexes_dict = {}

    with torch.no_grad():
        for batch_idx, (data, target_indexes, target_classes) in enumerate(tqdm_notebook(nograd_train_loader, desc='IncorrectCheck', leave=False)):
            optimizer.zero_grad()

            data = data.to(device)
            target_indexes = target_indexes.to(device)
            target_classes = target_classes.to(device)

            output = network(data)

            regular_indexes = get_indexes_where(target_indexes >= 0)
            corrupt_indexes = get_indexes_where(target_indexes < 0)

            regular_output = safe_argmax(output[regular_indexes])
            corrupt_output = safe_argmax(output[corrupt_indexes])
            regular_target_indexes = target_indexes[regular_indexes]
            corrupt_target_indexes = (-1) * target_indexes[corrupt_indexes] - 1  # (-1) * ((-1) * original index - 1) - 1 = original index
            regular_target_classes = target_classes[regular_indexes]
            corrupt_target_classes = target_classes[corrupt_indexes]

            regular_incorrect_indexes = get_indexes_where(regular_output != regular_target_classes)
            corrupt_incorrect_indexes = get_indexes_where(corrupt_output != corrupt_target_classes)

            regular_incorrect_indexes_dict.update({i.item(): j.item() for i, j in zip(regular_target_indexes[regular_incorrect_indexes],
                                                                                      regular_output[regular_incorrect_indexes])})
            corrupt_incorrect_indexes_dict.update({i.item(): j.item() for i, j in zip(corrupt_target_indexes[corrupt_incorrect_indexes],
                                                                                      corrupt_output[corrupt_incorrect_indexes])})

    return regular_incorrect_indexes_dict, corrupt_incorrect_indexes_dict

def test_once(network, optimizer, criterion, test_loader):
    # purely for test
    network.eval()
    epoch_loss = 0
    predict_results = []

    with torch.no_grad():
        for batch_idx, (data, target) in enumerate(tqdm_notebook(test_loader, desc='Test', leave=False)):
            optimizer.zero_grad()

            data = data.to(device)
            target = target.to(device)

            output = network(data)
            loss = criterion(output, target)

            predict_results.extend((output.argmax(dim=-1) == target).tolist())
            
            epoch_loss += loss.item() * data.size(0)

    return epoch_loss / len(test_loader.sampler), sum(predict_results) / len(predict_results)

In [29]:
def train(network_class, dataset_name, percent_corruption, train_loader, nograd_train_loader, test_loader, lr=0.01, lr_decay=0.95, max_epoch=20000, resume=0, **kwargs):
    network = network_class(**kwargs)
    optimizer = optim.SGD(network.parameters(), lr=lr, momentum=0.9)
    criterion = nn.CrossEntropyLoss()

    last_regular_idx_dict = {}
    last_corrupt_idx_dict = {}

    losses = {
        'train': [],
        'test': [],
    }

    if resume > 0:
        checkpoint = torch.load(f'{dataset_name}_results/seed{SEED}_{repr(network)}_cor{percent_corruption}_epoch{resume}.tar')
        network.load_state_dict(checkpoint['model_state_dict'])
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        last_regular_idx_dict = checkpoint['last_regular_idx_dict']
        last_corrupt_idx_dict = checkpoint['last_corrupt_idx_dict']
        losses = checkpoint['losses']

    scheduler = optim.lr_scheduler.StepLR(optimizer, step_size=1, gamma=lr_decay)

    network.to(device)

    for epoch_idx in range(resume, max_epoch):
        train_epoch_loss = train_once(network, optimizer, criterion, train_loader)

        regular_idx_dict, corrupt_idx_dict = get_incorrect_once(network, optimizer, nograd_train_loader)
        test_epoch_loss, test_accuracy = test_once(network, optimizer, criterion, test_loader)

        losses['train'].append(train_epoch_loss)
        losses['test'].append(test_epoch_loss)

        print(f'Epoch: {epoch_idx + 1:6} | Train Loss: {train_epoch_loss:.4f} | Test Loss: {test_epoch_loss:.4f} | Test Accuracy: {test_accuracy * 100:2.2f} | Pristine Incorrect: {len(regular_idx_dict):8} | Corrupt Incorrect: {len(corrupt_idx_dict):8}')

        if last_regular_idx_dict != regular_idx_dict or last_corrupt_idx_dict != corrupt_idx_dict:
            torch.save({
                'model_state_dict': network.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'last_regular_idx_dict': regular_idx_dict,
                'last_corrupt_idx_dict': corrupt_idx_dict,
                'losses': losses,
                'test_accuracy': test_accuracy,
            }, f'{dataset_name}_results/seed{SEED}_{repr(network)}_cor{percent_corruption}_epoch{epoch_idx + 1}.tar')
        
        if len(regular_idx_dict) == 0 and len(corrupt_idx_dict) == 0:
            break

        last_regular_idx_dict = regular_idx_dict
        last_corrupt_idx_dict = corrupt_idx_dict
        scheduler.step()

## Main

In [30]:
def run_all_corruption_levels(network_class, dataset_name, batch_size=128, nograd_batch_size=1000, shuffle=True, lr=0.01, lr_decay=0.95, max_epoch=20000, corruptions=None, resume_dict=None, **kwargs):
    resume_dict = resume_dict or {}
    corruptions = corruptions or [25, 50, 75, 100]
    in_size, out_size = get_io_params_for_dataset(dataset_name)
    kwargs.setdefault('in_size', in_size)
    kwargs.setdefault('out_size', out_size)

    Path(dataset_name).mkdir(parents=True, exist_ok=True)
    Path(dataset_name + '_results').mkdir(parents=True, exist_ok=True)

    train_set, test_set = get_data(dataset_name)
    sample_size = train_set.targets.size(0)

    torch.manual_seed(SEED)
    torch.cuda.manual_seed(SEED)
    torch.backends.cudnn.deterministic = True
    # these should be the only random ops we make here
    corruption_order = torch.randperm(sample_size)
    corrupted_labels = (train_set.targets + torch.randint(low=1, high=11, size=(sample_size,))) % 10

    for percent_corruption in corruptions:
        print(f'Corruption on Train Set: {percent_corruption}%')
        corrupted_train_set = Noisy(dataset_name=dataset_name,
                                    percent_corruption=percent_corruption,
                                    corruption_order=corruption_order,
                                    corrupted_labels=corrupted_labels)
        
        train_loader = DataLoader(corrupted_train_set, batch_size=batch_size, shuffle=shuffle)
        nograd_train_loader = DataLoader(corrupted_train_set, batch_size=nograd_batch_size, shuffle=shuffle)
        test_loader = DataLoader(test_set, batch_size=nograd_batch_size, shuffle=shuffle)

        train(network_class, dataset_name, percent_corruption,
              train_loader, nograd_train_loader, test_loader,
              lr=lr, lr_decay=lr_decay, max_epoch=max_epoch,
              resume=resume_dict.get(percent_corruption, 0), **kwargs)

In [34]:
run_all_corruption_levels(MLP, 'cifar10', width=512, depth=1, lr_decay=1.0, max_epoch=300, corruptions=[75, 100])

Files already downloaded and verified
Files already downloaded and verified
Corruption on Train Set: 75%
Files already downloaded and verified


Epoch:      1 | Train Loss: 2.2802 | Test Loss: 2.0859 | Test Accuracy: 35.08 | Pristine Incorrect:     7759 | Corrupt Incorrect:    33306


Epoch:      2 | Train Loss: 2.2546 | Test Loss: 2.0351 | Test Accuracy: 39.34 | Pristine Incorrect:     7132 | Corrupt Incorrect:    32893


Epoch:      3 | Train Loss: 2.2359 | Test Loss: 2.0106 | Test Accuracy: 39.92 | Pristine Incorrect:     6806 | Corrupt Incorrect:    32471


Epoch:      4 | Train Loss: 2.2167 | Test Loss: 1.9765 | Test Accuracy: 38.67 | Pristine Incorrect:     6609 | Corrupt Incorrect:    32087


...

Epoch:    296 | Train Loss: 0.6938 | Test Loss: 38.7344 | Test Accuracy: 10.37 | Pristine Incorrect:        0 | Corrupt Incorrect:     4569


Epoch:    297 | Train Loss: 0.8285 | Test Loss: 40.5866 | Test Accuracy: 9.56 | Pristine Incorrect:        0 | Corrupt Incorrect:     4827


Epoch:    298 | Train Loss: 0.7917 | Test Loss: 37.8990 | Test Accuracy: 10.20 | Pristine Incorrect:        0 | Corrupt Incorrect:     4497


Epoch:    299 | Train Loss: 0.7754 | Test Loss: 38.4757 | Test Accuracy: 9.65 | Pristine Incorrect:        0 | Corrupt Incorrect:     4552


Epoch:    300 | Train Loss: 0.8395 | Test Loss: 38.0512 | Test Accuracy: 10.46 | Pristine Incorrect:        0 | Corrupt Incorrect:     5072


In [35]:
run_all_corruption_levels(MLP, 'cifar10', width=512, depth=3, lr_decay=1.0, max_epoch=600)

Files already downloaded and verified
Files already downloaded and verified
Corruption on Train Set: 25%
Files already downloaded and verified


Epoch:      1 | Train Loss: 2.1139 | Test Loss: 1.7534 | Test Accuracy: 39.26 | Pristine Incorrect:    22581 | Corrupt Incorrect:    11226


Epoch:      2 | Train Loss: 1.9230 | Test Loss: 1.6380 | Test Accuracy: 43.61 | Pristine Incorrect:    20197 | Corrupt Incorrect:    11099


Epoch:      3 | Train Loss: 1.8411 | Test Loss: 1.5400 | Test Accuracy: 48.38 | Pristine Incorrect:    17698 | Corrupt Incorrect:    11017


Epoch:      4 | Train Loss: 1.7819 | Test Loss: 1.4774 | Test Accuracy: 50.27 | Pristine Incorrect:    16604 | Corrupt Incorrect:    10910


...

Epoch:    143 | Train Loss: 0.0038 | Test Loss: 15.5893 | Test Accuracy: 10.35 | Pristine Incorrect:        0 | Corrupt Incorrect:       43


Epoch:    144 | Train Loss: 0.0044 | Test Loss: 16.0917 | Test Accuracy: 10.41 | Pristine Incorrect:        0 | Corrupt Incorrect:        5


Epoch:    145 | Train Loss: 0.0015 | Test Loss: 16.0684 | Test Accuracy: 10.49 | Pristine Incorrect:        0 | Corrupt Incorrect:       10


Epoch:    146 | Train Loss: 0.0010 | Test Loss: 16.2624 | Test Accuracy: 10.32 | Pristine Incorrect:        0 | Corrupt Incorrect:        1


Epoch:    147 | Train Loss: 0.0005 | Test Loss: 16.4396 | Test Accuracy: 10.38 | Pristine Incorrect:        0 | Corrupt Incorrect:        0


In [37]:
for dataset in ['mnist', 'cifar10']:
    for d in [1, 3]:
        run_all_corruption_levels(MLP, dataset, width=512, depth=d, lr_decay=0.999, corruptions=[25, 50, 75])

Corruption on Train Set: 25%


Epoch:      1 | Train Loss: 1.3265 | Test Loss: 0.4598 | Test Accuracy: 93.96 | Pristine Incorrect:     2764 | Corrupt Incorrect:    13489


Epoch:      2 | Train Loss: 1.1617 | Test Loss: 0.4196 | Test Accuracy: 95.60 | Pristine Incorrect:     1863 | Corrupt Incorrect:    13491


Epoch:      3 | Train Loss: 1.1243 | Test Loss: 0.4155 | Test Accuracy: 96.19 | Pristine Incorrect:     1322 | Corrupt Incorrect:    13475


Epoch:      4 | Train Loss: 1.0970 | Test Loss: 0.3977 | Test Accuracy: 96.79 | Pristine Incorrect:     1156 | Corrupt Incorrect:    13473


...

Epoch:    136 | Train Loss: 0.0029 | Test Loss: 11.3613 | Test Accuracy: 20.86 | Pristine Incorrect:        6 | Corrupt Incorrect:       10


Epoch:    137 | Train Loss: 0.0019 | Test Loss: 11.5465 | Test Accuracy: 21.26 | Pristine Incorrect:        4 | Corrupt Incorrect:       15


Epoch:    138 | Train Loss: 0.0013 | Test Loss: 11.5588 | Test Accuracy: 21.81 | Pristine Incorrect:        0 | Corrupt Incorrect:        2


Epoch:    139 | Train Loss: 0.0004 | Test Loss: 11.6719 | Test Accuracy: 22.01 | Pristine Incorrect:        2 | Corrupt Incorrect:        2


Epoch:    140 | Train Loss: 0.0007 | Test Loss: 11.7224 | Test Accuracy: 22.04 | Pristine Incorrect:        0 | Corrupt Incorrect:        0
